1. Install all the necessary dependencies

In [ ]:
!pip install nltk
!pip install pandas
!pip install numpy
import nltk
nltk.download('stopwords')
nltk.download('punkt')
!pip install ipython-autotime
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer

import nltk
import os
import string
import numpy as np
import copy
import pandas as pd
import pickle

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [ ]:
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

2. Import the 20newsgroup dataset from sklearn.datasets

In [ ]:
from sklearn.datasets import fetch_20newsgroups
categories = ['alt.atheism', 'talk.religion.misc', 'comp.graphics', 'sci.space']
newsgroups_train = fetch_20newsgroups(subset='train',remove=('headers', 'footers', 'quotes'),categories=categories)

We are using the dataset for atheism,religion,graphics, space under 20 newsgroup dataset

In [ ]:
dataset=newsgroups_train.data
dataog=newsgroups_train.data

Regex for normalising sentences

In [ ]:
#regex for normalising sentences
pat1 = r'@[A-Za-z0-9]+' # this is to remove any text with @....
pat2 = r'https?://[A-Za-z0-9./]+'  # this is to remove the urls
combined_pattern = r'|'.join((pat1, pat2)) 
pat3 = r'[^a-zA-Z]' # to remove every other character except a-z & A-Z
combined_pattern2 = r'|'.join((combined_pattern,pat3)) # we combine pat1, pat2 and pat3 to pass it in the cleaning steps

Tokenize the sentences after removing @,case normalising and removing urls

In [ ]:
from nltk.tokenize import regexp_tokenize
import re
tokens_array=[]
for i in range(len(dataset)):
  dataset[i]=dataset[i].lower()
  stop=stopwords.words('english')
  dataset[i]=' '.join([word for word in dataset[i].split() if word not in stop])
  dataset[i] = re.sub(combined_pattern2,' ',dataset[i])
  dataset[i] =  re.sub(' {2,}', ' ', dataset[i])
  dataset[i]= re.sub('/\s+/', ' ',dataset[i])
  words=regexp_tokenize(dataset[i], "[\w']+")
  tokens_array.append(words)
print(tokens_array)

[['hi', 'i', 've', 'noticed', 'save', 'model', 'with', 'mapping', 'planes', 'positioned', 'carefully', 'ds', 'file', 'reload', 'restarting', 'ds', 'given', 'default', 'position', 'orientation', 'save', 'prj', 'file', 'positions', 'orientation', 'preserved', 'anyone', 'know', 'information', 'stored', 'ds', 'file', 'nothing', 'explicitly', 'said', 'manual', 'saving', 'texture', 'rules', 'prj', 'file', 'i', 'd', 'like', 'able', 'read', 'texture', 'rule', 'information', 'anyone', 'format', 'prj', 'file', 'cel', 'file', 'format', 'available', 'somewhere', 'rych'], ['seems', 'be', 'barring', 'evidence', 'contrary', 'koresh', 'simply', 'another', 'deranged', 'fanatic', 'thought', 'neccessary', 'take', 'whole', 'bunch', 'folks', 'him', 'children', 'all', 'satisfy', 'delusional', 'mania', 'jim', 'jones', 'circa', 'nope', 'fruitcakes', 'like', 'koresh', 'demonstrating', 'evil', 'corruption', 'centuries'], ['in', 'article', 'apr', 'sq', 'com', 'msb', 'sq', 'com', 'mark', 'brader', 'mb', 'mb', 'fi

Create the sentence again only with the lemmatized words so that we can create the posting list later

In [ ]:
from nltk import pos_tag
nltk.download('wordnet')
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
final_docs=[]
for text in tokens_array:
    outputarr=[]
    for word, tag in pos_tag(text):
      wntag = tag[0].lower()
      wntag = wntag if wntag in ['v', 'n', 'a', 'r'] else None
      lemma = lemmatizer.lemmatize(word, wntag) if wntag else word
      outputarr.append(lemma)
    final_docs.append(" ".join(outputarr))
print(final_docs)

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
['hi i ve notice save model with map plane position carefully ds file reload restart d give default position orientation save prj file position orientation preserve anyone know information store d file nothing explicitly say manual saving texture rule prj file i d like able read texture rule information anyone format prj file cel file format available somewhere rych', 'seem be bar evidence contrary koresh simply another derange fanatic thought neccessary take whole bunch folk him child all satisfy delusional mania jim jones circa nope fruitcake like koresh demonstrate evil corruption century', 'in article apr sq com msb sq com mark brader mb mb figure seem unlikely actually anything perijove jg sorry perijoves i m use talk language say periapsis apoapsis', 'request would like see charley wingate respond charley challenge and judge e mail appear quite you clear mr wingate intend co

Find the unique tokens in the dataset

In [ ]:
from enum import unique
#Creating tokens
unique_words=[]
for words in final_docs:
  tokens=words.split(" ")
  for word in tokens:
    if word not in unique_words and word!='':
      unique_words.append(word)
unique_words=sorted(unique_words)
print(unique_words)

['a', 'aa', 'aah', 'aan', 'aangeboden', 'aangegeven', 'aantal', 'aao', 'aap', 'aaplay', 'aarnet', 'aarseth', 'aas', 'aasked', 'aavso', 'ab', 'abandon', 'abba', 'abbasids', 'abberation', 'abbreviate', 'abbreviation', 'abc', 'abd', 'abdel', 'abduct', 'abdullah', 'abekas', 'aberdeen', 'aberration', 'abhor', 'abhorrent', 'abian', 'abide', 'ability', 'abiliy', 'abingdon', 'abiogenesis', 'abjure', 'ablazing', 'able', 'abn', 'abo', 'aboard', 'abode', 'abolish', 'abolishment', 'abolition', 'abolitionist', 'abomb', 'abord', 'abort', 'abortion', 'abound', 'about', 'above', 'abp', 'abraham', 'abrahamic', 'abruptly', 'abs', 'absence', 'absent', 'absolute', 'absolutely', 'absolutism', 'absolutist', 'absorb', 'absorber', 'absorbs', 'absorbtion', 'absorption', 'abstact', 'abstacted', 'abstinence', 'abstract', 'abstraction', 'absurd', 'absurdity', 'absurdly', 'abu', 'abundance', 'abundant', 'abundantly', 'abuse', 'abusive', 'abutaha', 'abyss', 'ac', 'acad', 'acadamy', 'academia', 'academic', 'academic

Build an inverted index on the terms

In [ ]:
inverted_index={}
for word in unique_words:
  inverted_index[word]=[]
  for i in range(len(final_docs)):
    words_in_doc=final_docs[i].split(" ")
    for w in range(len(words_in_doc)):
      if(words_in_doc[w]==word):
        inverted_index[word].append(i)
        break
print(inverted_index)

{'a': [46, 55, 57, 62, 69, 82, 87, 121, 122, 127, 131, 138, 144, 160, 175, 194, 203, 205, 220, 229, 235, 247, 250, 260, 264, 272, 274, 317, 322, 341, 347, 355, 366, 380, 384, 387, 389, 401, 403, 406, 411, 412, 416, 434, 436, 453, 454, 464, 502, 518, 519, 520, 531, 535, 536, 548, 553, 556, 577, 617, 630, 631, 640, 663, 701, 702, 746, 757, 764, 772, 776, 779, 784, 792, 799, 838, 839, 840, 848, 856, 868, 873, 874, 879, 882, 893, 905, 916, 945, 952, 955, 971, 981, 1017, 1026, 1039, 1041, 1042, 1052, 1073, 1077, 1088, 1093, 1097, 1117, 1130, 1135, 1147, 1168, 1170, 1176, 1178, 1180, 1214, 1217, 1246, 1266, 1267, 1280, 1287, 1295, 1309, 1322, 1326, 1328, 1354, 1357, 1359, 1361, 1375, 1376, 1407, 1411, 1425, 1433, 1453, 1471, 1481, 1500, 1507, 1527, 1533, 1538, 1551, 1552, 1563, 1568, 1574, 1578, 1582, 1589, 1590, 1602, 1605, 1614, 1619, 1642, 1645, 1650, 1656, 1669, 1682, 1689, 1697, 1708, 1723, 1733, 1739, 1746, 1753, 1756, 1757, 1758, 1760, 1774, 1779, 1803, 1808, 1823, 1848, 1866, 1875, 1

Building a positional index 

In [ ]:
positional_index={}
for word in unique_words:
  positional_index[word]={}
  for i in range(len(final_docs)):
    words_in_doc=final_docs[i].split(" ")
    for w in range(len(words_in_doc)):
      if(words_in_doc[w]==word):
        if i not in positional_index[word]:
          positional_index[word][i]=[w]
        else:
          positional_index[word][i].append(w)

Preprocess the query 

In [ ]:
def preprocess_query(sentence):
  sentence =sentence.lower()
  stop=stopwords.words('english')
  sentence=' '.join([word for word in sentence.split() if word not in stop])
  sentence = re.sub(combined_pattern2,' ',sentence)
  sentence =  re.sub(' {2,}', ' ',sentence)
  sentence= re.sub('/\s+/', ' ',sentence)
  words=regexp_tokenize(sentence, "[\w']+")
  processed_query=[]
  for word, tag in pos_tag(words):
    wntag = tag[0].lower()
    wntag = wntag if wntag in ['v', 'n', 'a', 'r'] else None
    lemma = lemmatizer.lemmatize(word, wntag) if wntag else word
    processed_query.append(lemma)
  return processed_query

In [ ]:
import numpy as np
sentence=input("Enter the query:\n")
inquery=np.array(preprocess_query(sentence))
print(inquery.size)

Enter the query:
religion god faith
3


Boolean AND query

In [ ]:
import time
start = time.time()
outputdocs={}
outputdocs=set()
for q in range(inquery.size):
  for word in unique_words:
    if inquery[q] in word:
      if q!=0:
        outputdocs=set(outputdocs)&(set(inverted_index[word]))
      else:
        outputdocs=inverted_index[word]
      break
end=time.time()
print("FOR AND BOOLEAN QUERY: \n The results matching the query are : time taken for search is "+str(end-start)+"\n")
count=1
for i in outputdocs:
    print("Doc No "+str(count)+" : " +dataog[i]+"\n")
    count+=1

FOR AND BOOLEAN QUERY: 
 The results matching the query are : time taken for search is 0.03813600540161133

Doc No 1 : recent developments dispute masonry among southern baptists posted summary bit listserv christia suppose might useful here note necessarily agree disagree follows present information short summary southern baptist named larry holly wrote book claiming freemasonry religion incompatible christianity mr holly s father rejects christianity mr holly blames masons sbc s home missions board includes interfaith witness department studies religions teach christ years ago ordered produce report masonry concluded religion therefore outside speciality however mr holly led movement people oppose masonry last year convention ordered hmb study masonry i got feeling saying you got wrong answer last time try better get answer want anyway there s bit infighting inappropriate actions dust settled report in nobody entirely happy it everybody seems willing live it sides saying things as th

Boolean OR query

In [ ]:
import time
start = time.time()
outputdocs={}
outputdocs=set()
for q in range(inquery.size):
  for word in unique_words:
    if inquery[q] in word:
      if q!=0:
        outputdocs=set(outputdocs)|(set(inverted_index[word]))
      else:
        outputdocs=inverted_index[word]
      break
end=time.time()
print("FOR AND BOOLEAN QUERY: \n The results matching the query are : time taken for search is "+str(end-start)+"\n")
count=1
for i in outputdocs:
    print("Doc No "+str(count)+" : " +dataog[i]+"\n")
    count+=1

FOR AND BOOLEAN QUERY: 
 The results matching the query are : time taken for search is 0.018480539321899414

Doc No 1 :  rick anderson replied letter with ra article c elp l c buffalo edu ra briefly something mentioned passing refer differing interpretations create say many christians may agree what really irrelevant base faith many people think one way another we bottom line truth regardless popularity opinions may irrelevant your personal beliefs or say bias relevant many others right the bottom line truth independant anyone else since proclaim truths self proclaimed appointee may ask authority this it says bible does bible say so you someone else interprets whether scripture doctrine conforms particular liking disapproval excuse moi line truths moved one bit persuade beliefs erroneous preachers truth net struck self righteous member wrecking crew positive message latter day saints whatsoever btw entire discussion reminds lot things said jesus pharisees ye hypocrite s ye preach lips 

Triword index ( find documents that contain atleast 3 of the query terms for longer documents )

In [ ]:
import time
start = time.time()
outputdocs={}
for q in range(inquery.size):
  for word in unique_words:
    if inquery[q] in word:
      for docid in inverted_index[word]:
        if docid not in outputdocs:
          outputdocs[docid]=1
        else:
          outputdocs[docid]+=1
      break
if len(outputdocs)>0:
  print("FOR TRIWORD MATCH: \nThe results matching the query are : time taken for search "+str(end-start)+"\n")
else:
  print("No docs found :(")
count=1
for key,val in outputdocs.items():
    if val>=3:
      print("Doc No "+str(count)+" : " +dataog[key]+"\n")
      count+=1

FOR TRIWORD MATCH: 
The results matching the query are : time taken for search -6.056572675704956

Doc No 1 : understand sympathize pain happened waco sad tradgedy take us christians though branch davidians organized religion cult led ego maniac cult leader christian faith stands shoulders one man lord lords king kings jesus christ btw david koresh jesus christ claimed god you malcolm lee 

Doc No 2 :  in mcclaryc snpq kb com mcclary com michael mcclary thought i d clear murky areas actually surviving driven nauvoo later carthage the mormons fortify utah still arm defend faith stockpile food well involved quite lot illegal activity including multiple and often underage wives for leaders practice still vogue splinters sect parallels koresh joseph smith striking they mean leaders lds church grant joseph smith still alive plenty accusations filed little bearing reality evidenced various verdicts studied lds history years now yet see prove lds leadership involved quote illegal activities p

**Bigram Index for Wildcard Query**

In [ ]:
withdollar=[]
for word in unique_words:
  newword="$"+word[:len(word)]+"$"
  withdollar.append(newword)
#print(withdollar)
bigram_index={}
for word in withdollar:
  bigrams=[word[i:i+2] for i in range(0, len(word))]
  for bg in bigrams:
    if bg in bigram_index:
      bigram_index[bg].append(word.replace('$',''))
    else:
      bigram_index[bg]=[word.replace('$','')]
print(bigram_index)

{'$a': ['a', 'aa', 'aah', 'aan', 'aangeboden', 'aangegeven', 'aantal', 'aao', 'aap', 'aaplay', 'aarnet', 'aarseth', 'aas', 'aasked', 'aavso', 'ab', 'abandon', 'abba', 'abbasids', 'abberation', 'abbreviate', 'abbreviation', 'abc', 'abd', 'abdel', 'abduct', 'abdullah', 'abekas', 'aberdeen', 'aberration', 'abhor', 'abhorrent', 'abian', 'abide', 'ability', 'abiliy', 'abingdon', 'abiogenesis', 'abjure', 'ablazing', 'able', 'abn', 'abo', 'aboard', 'abode', 'abolish', 'abolishment', 'abolition', 'abolitionist', 'abomb', 'abord', 'abort', 'abortion', 'abound', 'about', 'above', 'abp', 'abraham', 'abrahamic', 'abruptly', 'abs', 'absence', 'absent', 'absolute', 'absolutely', 'absolutism', 'absolutist', 'absorb', 'absorber', 'absorbs', 'absorbtion', 'absorption', 'abstact', 'abstacted', 'abstinence', 'abstract', 'abstraction', 'absurd', 'absurdity', 'absurdly', 'abu', 'abundance', 'abundant', 'abundantly', 'abuse', 'abusive', 'abutaha', 'abyss', 'ac', 'acad', 'acadamy', 'academia', 'academic', 'a

In [ ]:
query=input("Enter your wildcard query:")
start=time.time()
if query[0]=="*":
  query=query[1:len(query)]+"$"
  bigrams_query=[query[i:i+2] for i in range(0, len(query)-1)]
  print(bigrams_query)
elif query[len(query)-1]=="*":
  query="$"+query[0:len(query)-1]
  bigrams_query=[query[i:i+2] for i in range(0, len(query)-1)]
  print(bigrams_query)
else:
  leftq,rightq=query.split("*")
  leftq="$"+leftq[0:len(leftq)]
  rightq=rightq[0:len(rightq)]+"$"
  #print(leftq,rightq)
  bigrams_query_left=[leftq[i:i+2] for i in range(0, len(leftq)-1)]
  #print(bigrams_query_left)
  bigrams_query_right=[rightq[i:i+2] for i in range(0, len(rightq)-1)]
  #print(bigrams_query_right)
  bigrams_query_left.extend(bigrams_query_right)
  bigrams_query=bigrams_query_left
#print(bigrams_query)
length_bigram=len(bigrams_query)
bigramsdict={}
for bi in bigrams_query:
  if bi in bigram_index:
    for words in bigram_index[bi]:
      if words not in bigramsdict:
        bigramsdict[words]=1
      else:
        bigramsdict[words]+=1
docID=[]
for w,v in bigramsdict.items():
  if v==length_bigram:
    docID+=inverted_index[w]
docID=set(docID)
end=time.time()
print("FOR WILDCARD QUERY: \nThe results matching the query are : time taken for search "+str(end-start)+"\n")
count=1
for i in docID:
    print("Doc No "+str(count)+" : " +dataog[i]+"\n")
    count+=1

Enter your wildcard query:reli*
['$r', 're', 'el', 'li']
FOR WILDCARD QUERY: 
The results matching the query are : time taken for search 0.006792545318603516

Doc No 1 : false dichotomy claimed killing not religiously motivated i m saying that s wrong i m saying every killing religiously motivate spelled detail anyone else see contradiction paragraph sorry frank put quotes words posting qi b ec ap mchp sni de tell us different claim longer stand behind original claim say so 

Doc No 2 : true first news media seemed entranced new gizmos military using mention taped video transmissions missiles zeroed targets later especially bunker full civilians hit changed tone seemed stomach reality war innocent people really die maimed warfare like pro gulf war long nice clean smart missiles dropping military hqs pictures dead dying maimed civilians started cropping up naive hypocrites discussion blanket bombing a bombs deleted said militarily justified seems comments understood meaning morally just